## Arvato Customer segmentation and Classification

In this notebook we will work on the following task
- Exploratory Data Analysis
- Data Cleaning

In [6]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.offline import init_notebook_mode, iplot
import seaborn as sns
from matplotlib_venn import venn2, venn2_circles, venn2_unweighted
from matplotlib_venn import venn3, venn3_circles
from matplotlib import pyplot as plt
%matplotlib inline

from sklearn.impute import SimpleImputer

from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingRegressor, AdaBoostRegressor
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
import xgboost as xgb


from sklearn.model_selection import GridSearchCV


from sklearn.metrics import accuracy_score, roc_auc_score, confusion_matrix
from sklearn.model_selection import train_test_split, cross_val_score

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/arvato/Udacity_AZDIAS_052018.csv
/kaggle/input/arvato/Udacity_MAILOUT_052018_TRAIN.csv
/kaggle/input/arvato/DIAS Attributes - Values 2017.xlsx
/kaggle/input/arvato/Udacity_MAILOUT_052018_TEST.csv
/kaggle/input/arvato/Udacity_CUSTOMERS_052018.csv
/kaggle/input/arvato/DIAS Information Levels - Attributes 2017.xlsx
/kaggle/input/arvato-cleaned/Customers_cleaned.csv
/kaggle/input/arvato-cleaned/Azdias_cleaned.csv
/kaggle/input/arvato-cleaned/Customer_Additional_cleaned.csv


In [7]:
!pip install openpyxl

In [8]:
# Read the csv's 
# df_azdias: data about general population
# df_customers: data about customers
df_azdias = pd.read_csv('/kaggle/input/arvato/Udacity_AZDIAS_052018.csv',sep=';')
df_customers = pd.read_csv('/kaggle/input/arvato/Udacity_CUSTOMERS_052018.csv',sep=';')

In [9]:
ignore_unamed_cols = lambda x:'Unnamed' not in x

# attribute: contains data about columns description
attribute = pd.read_excel('../input/arvato/DIAS Attributes - Values 2017.xlsx',header=1,usecols=ignore_unamed_cols)
info = pd.read_excel('../input/arvato/DIAS Information Levels - Attributes 2017.xlsx',header=1,usecols=ignore_unamed_cols)

In [10]:
# The below class is used for preprocessing the data

class DataProcessing:
    def column_fill(self,df,column_name):
        '''
        input
        df: dataframe
        column_name: column that need to be filled
        
        output
        df:df filled with values for missing cells
        '''
        df[column_name] = df[column_name].ffill()
        return df
    
    def replace_with_nan(self,df,cols):
        '''
        Input
        df: Dataframe
        cols: columns
        replacing column values having 'X'or 'XX' with nan
        output: df
        '''
        df[cols] = df[cols].replace({"X": np.nan, "XX": np.nan})
        df[cols] = df[cols].astype(float)
        return df
    
    def replace_zero_nan(self,df,cols):
        '''
        Input
        df: Dataframe
        cols: columns
        replacing 0 with nan
        Output
        df
        '''
        df[cols] = df[cols].replace({0: np.nan})
        df[cols] = df[cols].astype(float)
        return df
    
    def convert_to_date(self,df,cols):
        '''
        Input
        df: dataframe
        cols:columns
        desc: convert to date
        Output
        df
        '''
        df[cols] = pd.to_datetime(df[cols])
        df[cols] = df[cols].map(lambda x: x.year)
        return df
    
    

    def get_unknown_repr(self,attrib, unknown_attributes_values):
        '''
        Input
        attrib: dataframe
        unknown_attribute_values: unknown values for attributes
        
        Output
        Returns a list of unknown values
        '''
        unknown = unknown_attributes_values[unknown_attributes_values["Attribute"] == attrib]["Value"]
        unknown = unknown.astype(str).str.cat(sep=",")
        unknown = [int(x) for x in unknown.split(",")]

        return [unknown]
    
    def replace_unknown_with_nan(self,val, unknown):
        '''
        Input
        val:values
        unknown: list of unknown values
        Output
        return nan values in case of unknown values
        '''
        if val in unknown:
            return np.nan
        else:
            return val
        
    def replace_unknowns(self,df, unknown_attributes_values, verbose=False):
        '''
        Input
        df: dataframe
        Output
        Replaces unknown values to 'np.nan' in all the columns provided in unknown_attributes_values list.
        '''
        for attrib in unknown_attributes_values.Attribute:
            unknown = self.get_unknown_repr(attrib, unknown_attributes_values)
            if verbose:
                print("Replacing {} to NaN in Attribute {}".format(unknown, attrib))
            if attrib in df.columns:
                df[attrib] = df[attrib].apply(self.replace_unknown_with_nan, args=(unknown))
        return df
    
    def get_missing_report(self,df):
        '''
        Input
        df: dataframe
        Output
        returns a dataframe with information about column-wise missing values percentages.
        '''
        missing_percen = df.isna().sum() * 100/ len(df)

        missing_percen_df = pd.DataFrame({"Attribute": df.columns,
                                         "Missing_Percentage": missing_percen}).reset_index(drop=True)
        return missing_percen_df
    
    def remove_columns(self,df, remove_cols):
        '''
        Input
        df: dataframe
        remove_cols: column list
        Drops given list of columns from df
        Output
        df:dataframe
        '''
        df = df.drop(remove_cols, axis = 1)
        return df
    
    def remove_missing_columns(self,df1, df2, df1_missing, df2_missing, threshold=30):
        '''
        Input
        df1: dataframe
        df2: dataframe
        df1: dataframe containing columns having missing values above a certain threshold
        df2: dataframe containing columns having missing values above a certain threshold
        Output
        Drops columns from df1 and df2 with given threshold.
        Uses df1_missing and df2_missing to determing which columns to remove.
        If df1_missing has more missing columns (missing_percentage > threshold),
        then df1_missing is taken as reference and vice versa.
        '''

        removable_cols1 = df1_missing[df1_missing.Missing_Percentage > threshold]
        removable_cols2 = df2_missing[df2_missing.Missing_Percentage > threshold]

        if len(removable_cols1) > len(removable_cols2):
            remove_cols = removable_cols1.Attribute.tolist()
        else:
            remove_cols = removable_cols2.Attribute.tolist()

        df1 = self.remove_columns(df1, remove_cols)
        df2 = self.remove_columns(df2, remove_cols)
        print(f"\t\tRemoved {len(remove_cols)} columns from given dataframes")

        return (df1, df2, remove_cols)
    
    def remove_missing_rows(self,df, threshold, name=""):
        '''
        Input
        df: dataframe
        threshold: threshold on number of missing features
        Output
        Drops rows with number of missing features 
        as per given threshold.
        '''
        total_rows = df.shape[0]

        df = df.dropna(thresh=df.shape[1]-threshold)

        removed_rows = total_rows - df.shape[0]

        print(f"\t\tRemoved {removed_rows} rows from {name} dataframe")

        # Reset index
        df = df.reset_index()
        del df['index']

        return df
    
    def fix_ost_west_col(self,df):
        '''
        Function to label encode the feature "OST_WEST_KZ"
        '''
        df["OST_WEST_KZ"] = df["OST_WEST_KZ"].replace({"W": 0, "O": 1})

        return df
    
    def fix_anrede_col(self,df):
        '''
        Input
        df:dataframe
        Output
        Returns df with label encoding of the feature "ANREDE_KZ"
        '''
        df["ANREDE_KZ"] = df["ANREDE_KZ"].replace({1: 0, 2: 1})

        return df
    
    def fix_cameo_intl_col(self,df):
        '''
        Input
        df: dataframe
        Output
        Returns df with  additional columns containing information from 'CAMEO_INTL_2015'
        '''
        df['CAMEO_INTL_2015_WEALTH'] = df['CAMEO_INTL_2015'].apply(lambda x: np.floor_divide(float(x), 10) if float(x) else np.nan)
        df['CAMEO_INTL_2015_FAMILY'] = df['CAMEO_INTL_2015'].apply(lambda x: np.mod(float(x), 10) if float(x) else np.nan)

        df.drop("CAMEO_INTL_2015", axis=1, inplace=True)
        return df
    
    def fix_wohnlage_col(self,df):
        '''
        Input
        df: dataframe
        Output
        Returns df after replacing '0' with np.nan from "WOHNLAGE" 
        '''
        df["WOHNLAGE"] = df["WOHNLAGE"].replace({0: np.nan})

        return df
    
    def impute_values(self,df,strategy="most_frequent"):
        '''
        Input
        df: dataframe
        strategy: imutation strategy
        Output
        Returns df after imputing values
        '''
        imputer = SimpleImputer(strategy=strategy)
        df = pd.DataFrame(imputer.fit_transform(df), columns = df.columns)
        return df
    
    
    def map_lp(self,df):
        '''
        Input
        df: dataframe
        Output
        Returns df after fixing the LP* columns as LP columns contains lot of redundant information
        '''
        convert_1 = {1: 'single', 2: 'couple', 3: 'singleparent', 4: 'singleparent', 5: 'singleparent', 
                  6: 'family', 7: 'family', 8: 'family', 9: 'multihousehold', 10: 'multihousehold', 11: 'multihousehold'}
        convert_2 = {'single':0, 'couple':1, 'singleparent':2, 'family':3, 'multihousehold':4}
        df["LP_FAMILIE_GROB"] = df["LP_FAMILIE_GROB"].map(convert_1)
        df["LP_FAMILIE_GROB"] = df["LP_FAMILIE_GROB"].map(convert_2)
    
        # LP_STATUS_GROB    
        convert_1 = {1: 'lowincome', 2: 'lowincome', 3: 'avgincome', 4: 'avgincome', 5: 'avgincome', 
                      6: 'independant', 7: 'independant', 8: 'houseowner', 9: 'houseowner', 10: 'topearner'}
        convert_2 = {'lowincome':0, 'avgincome':1, 'independant':2, 'houseowner':3, 'topearner':4}

        df["LP_STATUS_GROB"] = df["LP_STATUS_GROB"].map(convert_1)
        df["LP_STATUS_GROB"] = df["LP_STATUS_GROB"].map(convert_2)


        # LP_LEBENSPHASE_FEIN
        life_stages = {1: 'younger_age', 2: 'middle_age', 3: 'younger_age',
                  4: 'middle_age', 5: 'advanced_age', 6: 'retirement_age',
                  7: 'advanced_age', 8: 'retirement_age', 9: 'middle_age',
                  10: 'middle_age', 11: 'advanced_age', 12: 'retirement_age',
                  13: 'advanced_age', 14: 'younger_age', 15: 'advanced_age',
                  16: 'advanced_age', 17: 'middle_age', 18: 'younger_age',
                  19: 'advanced_age', 20: 'advanced_age', 21: 'middle_age',
                  22: 'middle_age', 23: 'middle_age', 24: 'middle_age',
                  25: 'middle_age', 26: 'middle_age', 27: 'middle_age',
                  28: 'middle_age', 29: 'younger_age', 30: 'younger_age',
                  31: 'advanced_age', 32: 'advanced_age', 33: 'younger_age',
                  34: 'younger_age', 35: 'younger_age', 36: 'advanced_age',
                  37: 'advanced_age', 38: 'retirement_age', 39: 'middle_age',
                  40: 'retirement_age'}

        wealth_scale = {1: 'low', 2: 'low', 3: 'average', 4: 'average', 5: 'low', 6: 'low',
                  7: 'average', 8: 'average', 9: 'average', 10: 'wealthy', 11: 'average',
                  12: 'average', 13: 'top', 14: 'average', 15: 'low', 16: 'average',
                  17: 'average', 18: 'wealthy', 19: 'wealthy', 20: 'top', 21: 'low',
                  22: 'average', 23: 'wealthy', 24: 'low', 25: 'average', 26: 'average',
                  27: 'average', 28: 'top', 29: 'low', 30: 'average', 31: 'low',
                  32: 'average', 33: 'average', 34: 'average', 35: 'top', 36: 'average',
                  37: 'average', 38: 'average', 39: 'top', 40: 'top'}

        df["Temp"] = df["LP_LEBENSPHASE_FEIN"]

        df["LP_LEBENSPHASE_FEIN"] = df["LP_LEBENSPHASE_FEIN"].map(life_stages)
        df["LP_LEBENSPHASE_GROB"] = df["Temp"].map(wealth_scale)

        life_stages = {'younger_age': 1, 'middle_age': 2, 'advanced_age': 3,
                'retirement_age': 4}
        wealth_scale = {'low': 1, 'average': 2, 'wealthy': 3, 'top': 4}

        df["LP_LEBENSPHASE_FEIN"] = df["LP_LEBENSPHASE_FEIN"].map(life_stages)
        df["LP_LEBENSPHASE_GROB"] = df["LP_LEBENSPHASE_GROB"].map(wealth_scale)
        return df

In [11]:
data_process = DataProcessing()

In [12]:
df_azdias.head()

LNR  AGER_TYP  AKT_DAT_KL  ALTER_HH  ALTER_KIND1  ALTER_KIND2  \
0  910215        -1         NaN       NaN          NaN          NaN   
1  910220        -1         9.0       0.0          NaN          NaN   
2  910225        -1         9.0      17.0          NaN          NaN   
3  910226         2         1.0      13.0          NaN          NaN   
4  910241        -1         1.0      20.0          NaN          NaN   

   ALTER_KIND3  ALTER_KIND4  ALTERSKATEGORIE_FEIN  ANZ_HAUSHALTE_AKTIV  ...  \
0          NaN          NaN                   NaN                  NaN  ...   
1          NaN          NaN                  21.0                 11.0  ...   
2          NaN          NaN                  17.0                 10.0  ...   
3          NaN          NaN                  13.0                  1.0  ...   
4          NaN          NaN                  14.0                  3.0  ...   

   VHN  VK_DHT4A  VK_DISTANZ  VK_ZG11  W_KEIT_KIND_HH  WOHNDAUER_2008  \
0  NaN       NaN         NaN      NaN             NaN             NaN   
1  4.0       8.0        11.0     10.0             3.0             9.0   
2  2.0       9.0         9.0      6.0             3.0             9.0   
3  0.0       7.0        10.0     11.0             NaN             9.0   
4  2.0       3.0         5.0      4.0             2.0             9.0   

   WOHNLAGE ZABEOTYP ANREDE_KZ ALTERSKATEGORIE_GROB  
0       NaN        3         1                    2  
1       4.0        5         2                    1  
2       2.0        5         2                    3  
3       7.0        3         2                    4  
4       3.0        4         1                    3  

[5 rows x 366 columns]

In [13]:
df_azdias.isnull().sum()

LNR                          0
AGER_TYP                     0
AKT_DAT_KL               73499
ALTER_HH                 73499
ALTER_KIND1             810163
                         ...  
WOHNDAUER_2008           73499
WOHNLAGE                 93148
ZABEOTYP                     0
ANREDE_KZ                    0
ALTERSKATEGORIE_GROB         0
Length: 366, dtype: int64

In [14]:
df_azdias.shape

(891221, 366)

In [15]:
df_customers.head()

LNR  AGER_TYP  AKT_DAT_KL  ALTER_HH  ALTER_KIND1  ALTER_KIND2  \
0    9626         2         1.0      10.0          NaN          NaN   
1    9628        -1         9.0      11.0          NaN          NaN   
2  143872        -1         1.0       6.0          NaN          NaN   
3  143873         1         1.0       8.0          NaN          NaN   
4  143874        -1         1.0      20.0          NaN          NaN   

   ALTER_KIND3  ALTER_KIND4  ALTERSKATEGORIE_FEIN  ANZ_HAUSHALTE_AKTIV  ...  \
0          NaN          NaN                  10.0                  1.0  ...   
1          NaN          NaN                   NaN                  NaN  ...   
2          NaN          NaN                   0.0                  1.0  ...   
3          NaN          NaN                   8.0                  0.0  ...   
4          NaN          NaN                  14.0                  7.0  ...   

   VK_ZG11  W_KEIT_KIND_HH  WOHNDAUER_2008  WOHNLAGE  ZABEOTYP  \
0      2.0             6.0             9.0       7.0         3   
1      3.0             0.0             9.0       NaN         3   
2     11.0             6.0             9.0       2.0         3   
3      2.0             NaN             9.0       7.0         1   
4      4.0             2.0             9.0       3.0         1   

       PRODUCT_GROUP  CUSTOMER_GROUP ONLINE_PURCHASE ANREDE_KZ  \
0  COSMETIC_AND_FOOD     MULTI_BUYER               0         1   
1               FOOD    SINGLE_BUYER               0         1   
2  COSMETIC_AND_FOOD     MULTI_BUYER               0         2   
3           COSMETIC     MULTI_BUYER               0         1   
4               FOOD     MULTI_BUYER               0         1   

  ALTERSKATEGORIE_GROB  
0                    4  
1                    4  
2                    4  
3                    4  
4                    3  

[5 rows x 369 columns]

In [16]:
df_customers.isnull().sum()

LNR                          0
AGER_TYP                     0
AKT_DAT_KL               46596
ALTER_HH                 46596
ALTER_KIND1             179886
                         ...  
PRODUCT_GROUP                0
CUSTOMER_GROUP               0
ONLINE_PURCHASE              0
ANREDE_KZ                    0
ALTERSKATEGORIE_GROB         0
Length: 369, dtype: int64

In [17]:
df_customers.shape

(191652, 369)

In [18]:
# We will look at the columns that are specific to azdias or customer df
azdias_columns = list(df_azdias.columns)
customer_columns = list(df_customers.columns)

print('Extra columns in customer')
print(set(customer_columns).difference(set(azdias_columns)))

print('Extra columns in azdias')
print(set(azdias_columns).difference(set(customer_columns)))

Extra columns in customer
{'ONLINE_PURCHASE', 'PRODUCT_GROUP', 'CUSTOMER_GROUP'}
Extra columns in azdias
set()


In [19]:
extra_customer_columns = [col for col in df_customers.columns if col not in df_azdias.columns]

In [20]:
df_customers[extra_customer_columns]

PRODUCT_GROUP CUSTOMER_GROUP  ONLINE_PURCHASE
0       COSMETIC_AND_FOOD    MULTI_BUYER                0
1                    FOOD   SINGLE_BUYER                0
2       COSMETIC_AND_FOOD    MULTI_BUYER                0
3                COSMETIC    MULTI_BUYER                0
4                    FOOD    MULTI_BUYER                0
...                   ...            ...              ...
191647  COSMETIC_AND_FOOD    MULTI_BUYER                0
191648           COSMETIC   SINGLE_BUYER                0
191649  COSMETIC_AND_FOOD    MULTI_BUYER                0
191650               FOOD   SINGLE_BUYER                0
191651  COSMETIC_AND_FOOD    MULTI_BUYER                0

[191652 rows x 3 columns]

As we can see the extra columns describe some customer buying behavior

In [21]:
# Now we will look at the attribute information about columns
attribute.head()

Attribute         Description Value                     Meaning
0  AGER_TYP  best-ager typology    -1                     unknown
1       NaN                 NaN     0  no classification possible
2       NaN                 NaN     1             passive elderly
3       NaN                 NaN     2            cultural elderly
4       NaN                 NaN     3   experience-driven elderly

we can see that each 'Attribute' and 'Description' value has multiple rows,we need to forward fill these columns

In [22]:
attribute = data_process.column_fill(attribute,'Attribute')
attribute = data_process.column_fill(attribute,'Description')

In [23]:
attribute.head(20)

Attribute                                   Description  Value  \
0               AGER_TYP                            best-ager typology     -1   
1               AGER_TYP                            best-ager typology      0   
2               AGER_TYP                            best-ager typology      1   
3               AGER_TYP                            best-ager typology      2   
4               AGER_TYP                            best-ager typology      3   
5   ALTERSKATEGORIE_GROB  age classification through prename analysis   -1, 0   
6   ALTERSKATEGORIE_GROB  age classification through prename analysis       1   
7   ALTERSKATEGORIE_GROB  age classification through prename analysis       2   
8   ALTERSKATEGORIE_GROB  age classification through prename analysis       3   
9   ALTERSKATEGORIE_GROB  age classification through prename analysis       4   
10  ALTERSKATEGORIE_GROB  age classification through prename analysis       9   
11              ALTER_HH                 main age within the household      0   
12              ALTER_HH                 main age within the household      1   
13              ALTER_HH                 main age within the household      2   
14              ALTER_HH                 main age within the household      3   
15              ALTER_HH                 main age within the household      4   
16              ALTER_HH                 main age within the household      5   
17              ALTER_HH                 main age within the household      6   
18              ALTER_HH                 main age within the household      7   
19              ALTER_HH                 main age within the household      8   

                             Meaning  
0                            unknown  
1         no classification possible  
2                    passive elderly  
3                   cultural elderly  
4          experience-driven elderly  
5                            unknown  
6                         < 30 years  
7                      30 - 45 years  
8                      46 - 60 years  
9                         > 60 years  
10             uniformly distributed  
11  unknown / no main age detectable  
12         01.01.1895 bis 31.12.1899  
13         01.01.1900 bis 31.12.1904  
14         01.01.1905 bis 31.12.1909  
15         01.01.1910 bis 31.12.1914  
16         01.01.1915 bis 31.12.1919  
17         01.01.1920 bis 31.12.1924  
18         01.01.1925 bis 31.12.1929  
19         01.01.1930 bis 31.12.1934

Attribute info description.
- Attribute - column name from df_azdias or df_customers
- Description - Description of column.
- Value - range of values for a column.
- Meaning - meaning of Value.


We will replace unknown values with np.nan


In [24]:
# let's see the warning columns on 18 and 19
warning_cols = list(df_azdias.columns[18:20])
print(warning_cols)
print(df_azdias[warning_cols].head())
print(df_azdias[warning_cols].dtypes)

['CAMEO_DEUG_2015', 'CAMEO_INTL_2015']
  CAMEO_DEUG_2015 CAMEO_INTL_2015
0             NaN             NaN
1             8.0            51.0
2             4.0            24.0
3             2.0            12.0
4             6.0            43.0
CAMEO_DEUG_2015    object
CAMEO_INTL_2015    object
dtype: object


In [25]:
print("values of ",warning_cols[0] )
print(df_azdias[warning_cols[0]].unique())
print("values of ",warning_cols[1] )
print(df_azdias[warning_cols[1]].unique())

values of  CAMEO_DEUG_2015
[nan 8.0 4.0 2.0 6.0 1.0 9.0 5.0 7.0 3.0 '4' '3' '7' '2' '8' '9' '6' '5'
 '1' 'X']
values of  CAMEO_INTL_2015
[nan 51.0 24.0 12.0 43.0 54.0 22.0 14.0 13.0 15.0 33.0 41.0 34.0 55.0 25.0
 23.0 31.0 52.0 35.0 45.0 44.0 32.0 '22' '24' '41' '12' '54' '51' '44'
 '35' '23' '25' '14' '34' '52' '55' '31' '32' '15' '13' '43' '33' '45'
 'XX']


We can see that we have 'X', 'XX' and 'nan' as values in these columns which have not been given in the description.

These values can be replaced with 'np.nan', as in the attributes dataframe it is described that any unknown values can be treated as '-1' but for simpicity we can consider this '-1' as 'np.nan'. Also there is inconsistency in the values i.e. some of them are strings and some of them are floats. We can to convert all of them into floats.


In [26]:
# We will convert the X, XX and nan into np.nan and other value into float
df_azdias = data_process.replace_with_nan(df_azdias,warning_cols)
df_customers = data_process.replace_with_nan(df_customers,warning_cols)

In [27]:
# We will now look at the column list
attributes_list  = attribute.Attribute.unique().tolist()
azdias_list = list(df_azdias.columns)
customers_list = list(df_customers.columns)

In [28]:
common = len(set(attributes_list) & set(azdias_list) & set(customers_list))
only_azdias = len(set(azdias_list) - set(attributes_list) - set(customers_list))
only_customers = len(set(customers_list) - set(attributes_list) - set(azdias_list))
only_attributes = len(set(attributes_list) - set(customers_list) - set(azdias_list))
attributes_and_azdias = len(set(attributes_list)&set(azdias_list)) - common
customers_and_attributes = len(set(attributes_list)&set(customers_list))- common
customers_and_azdias = len(set(azdias_list)&set(customers_list))- common

In [29]:
print("Columns only in azdias :",only_azdias)
print("Columns only in customers :",only_customers)
print("Columns only in attributes :",only_attributes)
print("Common columns across azdias,customers,attributes :",common)
print("Columns only in azdias and customers :",customers_and_azdias)
print("Columns only in attributes and customers :",customers_and_attributes)
print("Columns only in azdias and attributes :",attributes_and_azdias)

Columns only in azdias : 0
Columns only in customers : 3
Columns only in attributes : 42
Common columns across azdias,customers,attributes : 272
Columns only in azdias and customers : 94
Columns only in attributes and customers : 0
Columns only in azdias and attributes : 0


In [30]:
# Now let's look at the columns
df_azdias.head(100)

LNR  AGER_TYP  AKT_DAT_KL  ALTER_HH  ALTER_KIND1  ALTER_KIND2  \
0   910215        -1         NaN       NaN          NaN          NaN   
1   910220        -1         9.0       0.0          NaN          NaN   
2   910225        -1         9.0      17.0          NaN          NaN   
3   910226         2         1.0      13.0          NaN          NaN   
4   910241        -1         1.0      20.0          NaN          NaN   
..     ...       ...         ...       ...          ...          ...   
95  710299        -1         8.0       0.0          NaN          NaN   
96  710300        -1         1.0      19.0         11.0          NaN   
97  710302        -1         NaN       NaN          NaN          NaN   
98  745812        -1         4.0      17.0          NaN          NaN   
99  745813        -1         NaN       NaN          NaN          NaN   

    ALTER_KIND3  ALTER_KIND4  ALTERSKATEGORIE_FEIN  ANZ_HAUSHALTE_AKTIV  ...  \
0           NaN          NaN                   NaN                  NaN  ...   
1           NaN          NaN                  21.0                 11.0  ...   
2           NaN          NaN                  17.0                 10.0  ...   
3           NaN          NaN                  13.0                  1.0  ...   
4           NaN          NaN                  14.0                  3.0  ...   
..          ...          ...                   ...                  ...  ...   
95          NaN          NaN                   NaN                  5.0  ...   
96          NaN          NaN                   0.0                  7.0  ...   
97          NaN          NaN                   NaN                  NaN  ...   
98          NaN          NaN                  17.0                  2.0  ...   
99          NaN          NaN                   NaN                  NaN  ...   

    VHN  VK_DHT4A  VK_DISTANZ  VK_ZG11  W_KEIT_KIND_HH  WOHNDAUER_2008  \
0   NaN       NaN         NaN      NaN             NaN             NaN   
1   4.0       8.0        11.0     10.0             3.0             9.0   
2   2.0       9.0         9.0      6.0             3.0             9.0   
3   0.0       7.0        10.0     11.0             NaN             9.0   
4   2.0       3.0         5.0      4.0             2.0             9.0   
..  ...       ...         ...      ...             ...             ...   
95  3.0       7.0         8.0      5.0             6.0             3.0   
96  2.0       7.0        10.0      8.0             NaN             9.0   
97  NaN       NaN         NaN      NaN             NaN             NaN   
98  2.0       5.0         7.0      4.0             4.0             5.0   
99  NaN       NaN         NaN      NaN             NaN             NaN   

    WOHNLAGE ZABEOTYP  ANREDE_KZ  ALTERSKATEGORIE_GROB  
0        NaN        3          1                     2  
1        4.0        5          2                     1  
2        2.0        5          2                     3  
3        7.0        3          2                     4  
4        3.0        4          1                     3  
..       ...      ...        ...                   ...  
95       7.0        4          1                     1  
96       1.0        6          1                     2  
97       NaN        3          1                     2  
98       3.0        1          1                     3  
99       NaN        3          2                     2  

[100 rows x 366 columns]

In [31]:
# We will look at the LP columns
print(df_azdias.LP_FAMILIE_FEIN.unique())

print(df_azdias.LP_FAMILIE_GROB.unique())

print(df_azdias.LP_STATUS_GROB.unique())

print(df_azdias.LP_LEBENSPHASE_GROB.unique())

print(df_azdias.LP_LEBENSPHASE_FEIN.unique())

print(df_azdias.LP_STATUS_FEIN.unique())

[ 2.  5.  1.  0. 10.  7. 11.  3.  8.  4.  6. nan  9.]
[ 2.  3.  1.  0.  5.  4. nan]
[ 1.  2.  4.  5.  3. nan]
[ 4.  6.  1.  0. 10.  2.  3.  5.  7. 12. 11.  9.  8. nan]
[15. 21.  3.  0. 32.  8.  2.  5. 10.  4.  6. 23. 12. 20.  1. 11. 25. 13.
  7. 18. 31. 19. 38. 35. 30. 22. 14. 33. 29. 24. 28. 37. 26. 39. 27. 36.
  9. 34. nan 40. 16. 17.]
[ 1.  2.  3.  9.  4. 10.  5.  8.  6.  7. nan]




The columns LP_FAMILIE_FEIN, LP_FAMILIE_GROB, LP_LEBENSPHASE_GROB contains 0 which does not correspond to any category as the per the values in attributes. So we replace 0 with nan

Also, in these columns there is a lot of information that can be compressed, which is done by the following function.

- LP_FAMILIE_FEIN and LP_STATUS_FEIN give a fine categorization of the family type and family status. The same information in a broader spectrum is given by LP_FAMILIE_GROB and LP_STATUS_GROB. For this reason, for this analysis the columns LP_FAMILIE_FEIN and LP_STATUS_FEIN will be dropped.
    
- LP_LEBENSPHASE_GROB gives overall description of the life stage the person is in with respect to age and wealth and LP_LEBENSPHASE_FEIN gives a fine categorization of the persons age and financial status. Which means, these two columns are representing redundant information. Therefore, LP_LEBENSPHASE_GROB and LP_LEBENSPHASE_FEIN are restructed so that one of them contains information about age and the other one contains information about wealth.



In [32]:
columns = ['LP_FAMILIE_FEIN','LP_FAMILIE_GROB','LP_FAMILIE_GROB','LP_LEBENSPHASE_GROB','LP_LEBENSPHASE_FEIN','LP_STATUS_FEIN']
df_azdias[columns].head()

LP_FAMILIE_FEIN  LP_FAMILIE_GROB  LP_FAMILIE_GROB  LP_LEBENSPHASE_GROB  \
0              2.0              2.0              2.0                  4.0   
1              5.0              3.0              3.0                  6.0   
2              1.0              1.0              1.0                  1.0   
3              0.0              0.0              0.0                  0.0   
4             10.0              5.0              5.0                 10.0   

   LP_LEBENSPHASE_FEIN  LP_STATUS_FEIN  
0                 15.0             1.0  
1                 21.0             2.0  
2                  3.0             3.0  
3                  0.0             9.0  
4                 32.0             3.0

* We will convert 0 to np.nan as per the information in attribute.
We also need to convert them into proper category

In [33]:
# Now we will fix lp columns
df_azdias = data_process.map_lp(df_azdias)
df_customers = data_process.map_lp(df_customers)

Column EINGEFUEGT_AM gives information about date. This can be converted ito a datetime object to see its distribution.

In [34]:
# converttodata will extract the year from the date.
df_azdias = data_process.convert_to_date(df_azdias,'EINGEFUEGT_AM')
df_customers = data_process.convert_to_date(df_customers,'EINGEFUEGT_AM')

In [35]:
# Distribution of data according to date
x_az = df_azdias['EINGEFUEGT_AM']
x_cu = df_customers['EINGEFUEGT_AM']
x_label = "Year"
y_label = "Number of data points"
trace1 = go.Histogram(x=x_az,marker=dict(color='#ffdc51'),name='Azdias')
trace2 = go.Histogram(x=x_cu,marker=dict(color='#9932CC'),name='Customers')
layout = go.Layout(title="Distribution of data across years"
                   ,xaxis=dict(title=x_label),
                   yaxis=dict(title=y_label))
fig = go.Figure(data=[trace1,trace2],layout=layout)
iplot(fig)

Replacing unknown values

In [36]:
unknown_attributes_values = attribute[attribute["Meaning"] == "unknown"]
print(len(unknown_attributes_values))

232


In [37]:
# As we can see there are 232 unknown values
unknown_attributes_values.head()

Attribute                                        Description  \
0               AGER_TYP                                 best-ager typology   
5   ALTERSKATEGORIE_GROB       age classification through prename analysis    
33             ANREDE_KZ                                             gender   
40              BALLRAUM                     distance to next urban centre    
48              BIP_FLAG  business-flag indicating companies in the buil...   

    Value  Meaning  
0      -1  unknown  
5   -1, 0  unknown  
33  -1, 0  unknown  
40     -1  unknown  
48     -1  unknown

In [38]:
# we will replace unknown values with np.nan
df_azdias = data_process.replace_unknowns(df_azdias, unknown_attributes_values, verbose=True)
df_customers = data_process.replace_unknowns(df_customers, unknown_attributes_values, verbose=True)

Replacing [[-1]] to NaN in Attribute AGER_TYP
Replacing [[-1, 0]] to NaN in Attribute ALTERSKATEGORIE_GROB
Replacing [[-1, 0]] to NaN in Attribute ANREDE_KZ
Replacing [[-1]] to NaN in Attribute BALLRAUM
Replacing [[-1]] to NaN in Attribute BIP_FLAG
Replacing [[-1]] to NaN in Attribute CAMEO_DEUG_2015
Replacing [[-1]] to NaN in Attribute CAMEO_DEUINTL_2015
Replacing [[0]] to NaN in Attribute CJT_GESAMTTYP
Replacing [[-1]] to NaN in Attribute D19_KK_KUNDENTYP
Replacing [[-1]] to NaN in Attribute EWDICHTE
Replacing [[-1]] to NaN in Attribute FINANZTYP
Replacing [[-1]] to NaN in Attribute FINANZ_ANLEGER
Replacing [[-1]] to NaN in Attribute FINANZ_HAUSBAUER
Replacing [[-1]] to NaN in Attribute FINANZ_MINIMALIST
Replacing [[-1]] to NaN in Attribute FINANZ_SPARER
Replacing [[-1]] to NaN in Attribute FINANZ_UNAUFFAELLIGER
Replacing [[-1]] to NaN in Attribute FINANZ_VORSORGER
Replacing [[-1, 0]] to NaN in Attribute GEBAEUDETYP
Replacing [[-1, 0]] to NaN in Attribute GEOSCORE_KLS7
Replacing [[-1

Replacing [[-1]] to NaN in Attribute KBA13_KW_70
Replacing [[-1]] to NaN in Attribute KBA13_KW_61_120
Replacing [[-1]] to NaN in Attribute KBA13_KW_80
Replacing [[-1]] to NaN in Attribute KBA13_KW_90
Replacing [[-1]] to NaN in Attribute KBA13_KW_110
Replacing [[-1]] to NaN in Attribute KBA13_KW_120
Replacing [[-1]] to NaN in Attribute KBA13_KW_121
Replacing [[-1]] to NaN in Attribute KBA13_MAZDA
Replacing [[-1]] to NaN in Attribute KBA13_MERCEDES
Replacing [[-1]] to NaN in Attribute KBA13_MOTOR
Replacing [[-1]] to NaN in Attribute KBA13_NISSAN
Replacing [[-1]] to NaN in Attribute KBA13_OPEL
Replacing [[-1]] to NaN in Attribute KBA13_PEUGEOT
Replacing [[-1]] to NaN in Attribute KBA13_RENAULT
Replacing [[-1]] to NaN in Attribute KBA13_SEG_GELAENDEWAGEN
Replacing [[-1]] to NaN in Attribute KBA13_SEG_GROSSRAUMVANS
Replacing [[-1]] to NaN in Attribute KBA13_SEG_KLEINST
Replacing [[-1]] to NaN in Attribute KBA13_SEG_KLEINWAGEN
Replacing [[-1]] to NaN in Attribute KBA13_SEG_KOMPAKTKLASSE
Repl

Replacing [[-1, 9]] to NaN in Attribute KBA05_VORB2
Replacing [[-1, 9]] to NaN in Attribute KBA05_ZUL1
Replacing [[-1, 9]] to NaN in Attribute KBA05_ZUL2
Replacing [[-1, 9]] to NaN in Attribute KBA05_ZUL3
Replacing [[-1, 9]] to NaN in Attribute KBA05_ZUL4
Replacing [[-1]] to NaN in Attribute KBA13_ALTERHALTER_30
Replacing [[-1]] to NaN in Attribute KBA13_ALTERHALTER_45
Replacing [[-1]] to NaN in Attribute KBA13_ALTERHALTER_60
Replacing [[-1]] to NaN in Attribute KBA13_ALTERHALTER_61
Replacing [[-1]] to NaN in Attribute KBA13_AUDI
Replacing [[-1]] to NaN in Attribute KBA13_AUTOQUOTE
Replacing [[-1]] to NaN in Attribute KBA13_BJ_1999
Replacing [[-1]] to NaN in Attribute KBA13_BJ_2000
Replacing [[-1]] to NaN in Attribute KBA13_BJ_2004
Replacing [[-1]] to NaN in Attribute KBA13_BJ_2006
Replacing [[-1]] to NaN in Attribute KBA13_BJ_2008
Replacing [[-1]] to NaN in Attribute KBA13_BJ_2009
Replacing [[-1]] to NaN in Attribute KBA13_BMW
Replacing [[-1]] to NaN in Attribute KBA13_CCM_1000
Replac

We will look at the missing values

In [39]:
# Missing values
df_azdias_missing_report = data_process.get_missing_report(df_azdias)
df_customers_missing_report = data_process.get_missing_report(df_customers)

In [41]:
fig = make_subplots(rows=1, cols=3, start_cell="bottom-left")

x_az = df_azdias_missing_report['Attribute']
y_az = df_azdias_missing_report['Missing_Percentage']
trace1 = go.Bar(x=y_az,y=x_az,orientation='h',width=1,marker_line_color='rgb(8,48,107)',
                  marker_line_width=.5,marker=dict(color='#ffdc51'),name='Azdias')

x_cu = df_customers_missing_report['Attribute']
y_cu = df_customers_missing_report['Missing_Percentage']
trace2 = go.Bar(x=y_cu,y=x_cu,orientation='h',width=1,marker_line_color='rgb(8,48,107)',
                  marker_line_width=.5,marker=dict(color='#9932CC'),name='Customers')


fig.update_layout(
    autosize=False,
    width=1000,
    height=8000,
     bargap=.5)

fig.add_trace(trace1,
              row=1, col=1)

fig.add_trace(trace2,
              row=1, col=3)

iplot(fig)

There is an overlap in both Azdias and Customers data i.e. data is missing from same columns.
Also the percentage of missing values in Azdias and Customers coincide a lot, which confirms that customers data is a subset of azdias data.

In [42]:
# We will remove columns that have more than 30% of data missing.
print("Azdias")
print(df_azdias_missing_report[df_azdias_missing_report['Missing_Percentage']>30])
print(len(df_azdias_missing_report[df_azdias_missing_report['Missing_Percentage']>30]))
print("Customers")
print(df_customers_missing_report[df_customers_missing_report['Missing_Percentage']>30])
print(len(df_customers_missing_report[df_customers_missing_report['Missing_Percentage']>30]))

Azdias
        Attribute  Missing_Percentage
1        AGER_TYP           76.019640
4     ALTER_KIND1           90.904837
5     ALTER_KIND2           96.690047
6     ALTER_KIND3           99.307691
7     ALTER_KIND4           99.864792
100     EXTSEL992           73.399639
129  KBA05_BAUMAX           53.468668
300  KK_KUNDENTYP           65.596749
349      TITEL_KZ           99.757636
9
Customers
        Attribute  Missing_Percentage
1        AGER_TYP           48.059504
4     ALTER_KIND1           93.860748
5     ALTER_KIND2           97.338927
6     ALTER_KIND3           99.334732
7     ALTER_KIND4           99.876860
100     EXTSEL992           44.498883
129  KBA05_BAUMAX           57.153069
300  KK_KUNDENTYP           58.406382
301           KKK           31.340137
326      REGIOTYP           31.340137
349      TITEL_KZ           98.793647
11


As we can see azdias has 9 columns and customers have 11 columns having more than 30% data misising. We will remove 11 columns of customers from both azdias and customers

In [43]:
# Plot of missing values
fig = make_subplots(rows=1, cols=3, start_cell="bottom-left")
df_threshold_azdias = df_azdias_missing_report[df_azdias_missing_report['Missing_Percentage']>30]
df_threshold_customers = df_customers_missing_report[df_customers_missing_report['Missing_Percentage']>30]
x_az = df_threshold_azdias['Attribute']
y_az = df_threshold_azdias['Missing_Percentage']
trace1 = go.Bar(x=y_az,y=x_az,orientation='h',width=1,marker_line_color='rgb(8,48,107)',
                  marker_line_width=.5,marker=dict(color='#ffdc51'),name='Azdias')

x_cu = df_threshold_customers['Attribute']
y_cu = df_threshold_customers['Missing_Percentage']
trace2 = go.Bar(x=y_cu,y=x_cu,orientation='h',width=1,marker_line_color='rgb(8,48,107)',
                  marker_line_width=.5,marker=dict(color='#9932CC'),name='Customers')


fig.update_layout(
    autosize=False,
#     width=1000,
#     height=200,
     bargap=.5)

fig.add_trace(trace1,
              row=1, col=1)

fig.add_trace(trace2,
              row=1, col=3)

iplot(fig)

In [ ]:
# this function will remove columns having more than 30% data missing.
df_azdias, df_customers, removed_cols = data_process.remove_missing_columns(df_azdias, df_customers, df_customers_missing_report, df_azdias_missing_report)

Now we will look at the missing values in rows

In [ ]:
df_azdias_missing_row = df_azdias.isnull().sum(axis=1)
df_customers_missing_row = df_customers.isnull().sum(axis=1)
x_az = df_azdias_missing_row.values
x_cu = df_customers_missing_row.values
x_label = "number of features"
y_label = "Number of missing data points"
trace1 = go.Histogram(x=x_az,marker=dict(color='#ffdc51'),name='Azdias',nbinsx=20)
trace2 = go.Histogram(x=x_cu,marker=dict(color='#9932CC'),name='Customers',nbinsx=20)
layout = go.Layout(title="Distribution of data across years"
                   ,xaxis=dict(title=x_label),
                   yaxis=dict(title=y_label))
fig = go.Figure(data=[trace1,trace2],layout=layout)
iplot(fig)

As you can see most of the data have less than 50 features missing.
We will remove row which have more than 50 features missing.

In [ ]:
df_customers = data_process.remove_missing_rows(df_customers, threshold=50)
df_azdias = data_process.remove_missing_rows(df_azdias, threshold=50)

In [ ]:
print("Number of rows in azdias: ",df_azdias.shape[0])
print("Number of rows in customers: ",df_customers.shape[0])

In [ ]:
df_azdias.shape,df_customers.shape

In [ ]:
# Let's look at columns having 'object' datatype
print("Azdias")
azdias_obj_cols = df_azdias.columns[df_azdias.dtypes=="object"]
print(azdias_obj_cols)
print("Customers")
customers_obj_cols = df_customers.columns[df_customers.dtypes=="object"]
print(customers_obj_cols)


In [ ]:
df_azdias[azdias_obj_cols].head()

In [ ]:
for col in azdias_obj_cols:
    print(df_azdias[col].value_counts())

- D19_LETZTER_KAUF_BRANCHE - contains information about the last branch they made a purchase.
- CAMEO_DEU_2015 - Gives information about specific group a person belongs to.
- OST_WEST_KZ - contains information about the history of the person i.e. which part of Germany they belonged to before unification. We can encode values in this column with pd_dummies or a label encoder.

- We will drop 'D19_LETZTER_KAUF_BRANCHE' and 'CAMEO_DEU_2015'.
- We will convert 'OST_WEST_KZ' into binary.

In [ ]:
for col in azdias_obj_cols:
    print(attribute[attribute.Attribute == col].head(5))

We will remove "LP_FAMILIE_FEIN", "LP_STATUS_FEIN" also as we have already included the its information through map_lp().

In [ ]:
remove_extra_cols = ["D19_LETZTER_KAUF_BRANCHE", "CAMEO_DEU_2015", "LP_FAMILIE_FEIN", "LP_STATUS_FEIN"]

df_azdias = data_process.remove_columns(df_azdias, remove_extra_cols)
df_customers = data_process.remove_columns(df_customers, remove_extra_cols)

In [ ]:
# converting 'OST_WEST_KZ' into binary
df_azdias = data_process.fix_ost_west_col(df_azdias)
df_customers = data_process.fix_ost_west_col(df_customers)

In [ ]:
df_azdias['ANREDE_KZ'].head()

In [ ]:
# converting the 'ANREDE_KZ'into binary
df_azdias = data_process.fix_anrede_col(df_azdias)
df_customers = data_process.fix_anrede_col(df_customers)

- Converting  CAMEO_INTL_2015 colums
- It contains two types of information contained into one column. It can be further divided into two seperate columns

In [ ]:
df_azdias = data_process.fix_cameo_intl_col(df_azdias)
df_customers = data_process.fix_cameo_intl_col(df_customers)

In [ ]:
df_azdias['WOHNLAGE'].unique()

In [ ]:
attribute[attribute.Attribute=='WOHNLAGE']

The column WOHNLAGE contains value - 0 for - no score calculated, while all other values represent some score. This value can be replaced with NaN.

In [ ]:
df_azdias = data_process.fix_wohnlage_col(df_azdias)
df_customers = data_process.fix_wohnlage_col(df_customers)

We will remove extra columns from customers

In [ ]:
extra_customer_columns= list(set(customer_columns).difference(set(azdias_columns)))

In [ ]:
df_extra_customer = df_customers[extra_customer_columns]
df_customers= df_customers.drop(extra_customer_columns, axis = 1)

In [ ]:
print(df_azdias.shape,df_customers.shape,df_extra_customer.shape)

Now we will impute missing values.

In [ ]:
imputer = SimpleImputer(strategy="most_frequent")
df_azdias = pd.DataFrame(imputer.fit_transform(df_azdias), columns = df_azdias.columns)
df_customers = pd.DataFrame(imputer.transform(df_customers), columns = df_customers.columns)

We will store the clean dataframes.

In [ ]:
df_azdias.to_csv('Azdias_cleaned.csv', index=False)
df_customers.to_csv('Customers_cleaned.csv', index=False)
df_extra_customer.to_csv('Customer_Additional_cleaned.csv', index=False)